In [3]:
# ok I want with confidence, all zip codes reported by census, and their lat/lngs
import pandas as pd
import plotly.express as px
from IPython.display import display
from scipy.stats import zscore
from lib.census_helper import load_sweetened_zips

us_zips = load_sweetened_zips()
us_zips

_zip       _lat       _lng  _census_total
0      47337  39.802754 -85.437285            203
1      47514  38.148600 -86.594016           1559
2      46045  40.289610 -86.148659             93
3      46704  41.103660 -85.292142             60
4      47585  38.268350 -87.158083            592
...      ...        ...        ...            ...
32918  37932  35.917299 -84.198787          14527
32919  37341  35.219931 -85.073003          12085
32920  37849  36.054050 -84.048488          25459
32921  37754  36.139099 -84.029801           4729
32922  37806  36.084693 -83.727987           2868

[32923 rows x 4 columns]

In [5]:
df = us_zips

# RARE_DISEASE_PCT = 0.0006
RARE_DISEASE_PCT = 1 * (10**-4)
FUNNEL = .01

df['_rare_total'] = df['_census_total'].apply(lambda x: int(x * RARE_DISEASE_PCT))
df['_rare_target'] = df['_rare_total'].apply(lambda x: int(x * FUNNEL))
# df = df[df['_rare_predicted'] > 0].reset_index(drop=True)
display(df.head())
# may want more complex sampling method but hey this is def simpliest

px.scatter_mapbox(
    df, lat="_lat", lon="_lng", size_max=15, mapbox_style="open-street-map", 
    height=800, zoom=3, 
    color="_rare_predicted",
    title=f"Predicted Rare Population Total | {RARE_DISEASE_PCT}% | Total n={df['_rare_predicted'].sum()}  {df['_rare_target'].sum()}"
).show()

_zip       _lat       _lng  _census_total  _rare_predicted  _rare_target  \
0  47337  39.802754 -85.437285            203                0             0   
1  47514  38.148600 -86.594016           1559                0             0   
2  46045  40.289610 -86.148659             93                0             0   
3  46704  41.103660 -85.292142             60                0             0   
4  47585  38.268350 -87.158083            592                0             0   

   _rare_total  
0            0  
1            0  
2            0  
3            0  
4            0

In [24]:
px.histogram(df, x='_rare_total')

In [41]:
px.histogram(df, x='_z_census_total')

In [44]:
# so a rare disease is defined as < 200,000 by Orphan Drug Act

 
3*(10**8)

300000000

In [49]:
rare_disease_scalar = 2*(10**5) / df['_census_total'].sum()
rare_disease_scalar

0.0006401601199219635

In [54]:
df["_pct"] = df["_census_total"].apply(lambda x: x/df["_census_total"].sum())
df = df.sort_values("_pct", ascending=False).reset_index(drop=True)
df['_cumm_pct'] = df['_pct'].cumsum()
df

_zip       _lat        _lng  _census_total  _z_census_total      _pct  \
0      60629  41.775414  -87.711487         113916         7.580294  0.000365   
1      79936  31.773676 -106.295415         111086         7.374865  0.000356   
2      11368  40.749737  -73.853045         109931         7.291023  0.000352   
3      00926  18.348601  -66.053929         108862         7.213425  0.000348   
4      90650  33.907790 -118.082487         105549         6.972935  0.000338   
...      ...        ...         ...            ...              ...       ...   
32918  55155  44.951919  -93.099362              0        -0.688838  0.000000   
32919  55905  44.055948  -92.525906              0        -0.688838  0.000000   
32920  11451  40.701188  -73.795778              0        -0.688838  0.000000   
32921  20520  38.894700  -77.048481              0        -0.688838  0.000000   
32922  06020  41.862788  -72.909934              0        -0.688838  0.000000   

       _cumm_pct  
0       0.000365  
1       0.000720  
2       0.001072  
3       0.001420  
4       0.001758  
...          ...  
32918   1.000000  
32919   1.000000  
32920   1.000000  
32921   1.000000  
32922   1.000000  

[32923 rows x 7 columns]

In [56]:
df['_census_total'].describe()

count     32923.000000
mean       9489.470461
std       13776.262722
min           0.000000
25%         753.500000
50%        2851.000000
75%       13075.000000
max      113916.000000
Name: _census_total, dtype: float64

In [55]:
px.scatter(df.reset_index(), x='index', y='_cumm_pct', title="The ")